In [0]:
%sh
pip install  textblob googletrans nltk langdetect emoji tweepy wordcloud vaderSentiment

  Created wheel for googletrans: filename=googletrans-3.0.0-py3-none-any.whl size=15734 sha256=d74bd1cd0f25d779bac48bf25c7f38a06ad81f576162093a5e4cc12519fe9dba
  Stored in directory: /root/.cache/pip/wheels/27/f3/32/d4859d40071f07a5df0ab6fdc0076e78a8a786625dde2b4b2f
  Created wheel for langdetect: filename=langdetect-1.0.9-py3-none-any.whl size=993242 sha256=f60579b257b8df1f902ce806be5f51e5cf3d1fd74203267561eef51d0f1cde31
  Stored in directory: /root/.cache/pip/wheels/d1/c1/d9/7e068de779d863bc8f8fc9467d85e25cfe47fa5051fff1a1bb
  Created wheel for emoji: filename=emoji-2.2.0-py3-none-any.whl size=234925 sha256=3e0a9c76b9fded980ba3229b5316815bb6f9ffd23f87395b859e0f8615fd8973
  Stored in directory: /root/.cache/pip/wheels/9a/b8/0f/f580817231cbf59f6ade9fd132ff60ada1de9f7dc85521f857
Successfully built googletrans langdetect emoji
  Attempting uninstall: idna
    Found existing installation: idna 3.2
    Not uninstalling idna at /databricks/python3/lib/python3.9/site-packages, outside enviro

In [0]:
Package_path =''
import sys
for path in sys.path:
  if path.startswith('/local_disk0/.ephemeral_nfs/envs/'):
    Package_path=path

In [0]:
t="""
# -*- coding: utf-8 -*-

#Translator module that uses the Google Translate API.

#Adapted from Terry Yin's google-translate-python.
#Language detection added by Steven Loria.

from __future__ import absolute_import

import codecs
import json
import re

from textblob.compat import PY2, request, urlencode
from textblob.exceptions import TranslatorError, NotTranslated


class Translator(object):

    #A language translator and detector.

    #Usage:
    #::
        #>>> from textblob.translate import Translator
        #>>> t = Translator()
        #>>> t.translate('hello', from_lang='en', to_lang='fr')
        #u'bonjour'
        #>>> t.detect("hola")
        #u'es' 

    url = "http://translate.google.com/translate_a/t?client=te&format=html&dt=bd&dt=ex&dt=ld&dt=md&dt=qca&dt=rw&dt=rm&dt=ss&dt=t&dt=at&ie=UTF-8&oe=UTF-8&otf=2&ssel=0&tsel=0&kc=1"

    headers = {
        'Accept': '*/*',
        'Connection': 'keep-alive',
        'User-Agent': (
            'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_6_8) '
            'AppleWebKit/535.19 (KHTML, like Gecko) Chrome/18.0.1025.168 Safari/535.19')
    }

    def translate(self, source, from_lang='auto', to_lang='en', host=None, type_=None):
        #Translate the source text from one language to another.
        if PY2:
            source = source.encode('utf-8')
        data = {"q": source}
        url = u'{url}&sl={from_lang}&tl={to_lang}&hl={to_lang}&tk={tk}&client={client}'.format(
            url=self.url,
            from_lang=from_lang,
            to_lang=to_lang,
            tk=_calculate_tk(source),
            client="te",
        )
        response = self._request(url, host=host, type_=type_, data=data)
        result = json.loads(response)[0]
        if isinstance(result, list):
            try:
                result = result[0]  # ignore detected language
            except IndexError:
                pass
        self._validate_translation(source, result)
        return result

    def detect(self, source, host=None, type_=None):
        #Detect the source text's language.
        if PY2:
            source = source.encode('utf-8')
        if len(source) < 3:
            raise TranslatorError('Must provide a string with at least 3 characters.')
        data = {"q": source}
        url = u'{url}&sl=auto&tk={tk}&client={client}'.format(
            url=self.url,
            tk=_calculate_tk(source),
            client="te",
        )
        response = self._request(url, host=host, type_=type_, data=data)
        result, language = json.loads(response)
        return language

    def _validate_translation(self, source, result):
        #Validate API returned expected schema, and that the translated text
        #is different than the original string.
     
    
        if not result:
            raise NotTranslated('Translation API returned and empty response.')
        if PY2:
            result = result.encode('utf-8')
        #if result.strip() == source.strip():
            #raise NotTranslated('Translation API returned the input string unchanged.')

    def _request(self, url, host=None, type_=None, data=None):
        encoded_data = urlencode(data).encode('utf-8')
        req = request.Request(url=url, headers=self.headers, data=encoded_data)
        if host or type_:
            req.set_proxy(host=host, type=type_)
        resp = request.urlopen(req)
        content = resp.read()
        return content.decode('utf-8')


def _unescape(text):
    #Unescape unicode character codes within a string.
    pattern = r'\\{1,2}u[0-9a-fA-F]{4}'
    return re.sub(pattern, lambda x: codecs.getdecoder('unicode_escape')(x.group())[0], text)


def _calculate_tk(source):
    #Reverse engineered cross-site request protection.
    # Source: https://github.com/soimort/translate-shell/issues/94#issuecomment-165433715
    # Source: http://www.liuxiatool.com/t.php

    def c_int(x, nbits=32):
        #C cast to int32, int16, int8...
        return (x & ((1 << (nbits - 1)) - 1)) - (x & (1 << (nbits - 1)))

    def c_uint(x, nbits=32):
        #C cast to uint32, uint16, uint8... 
        return x & ((1 << nbits) - 1)

    tkk = [406398, 561666268 + 1526272306]
    b = tkk[0]

    if PY2:
        d = map(ord, source)
    else:
        d = source.encode('utf-8')

    def RL(a, b):
        for c in range(0, len(b) - 2, 3):
            d = b[c + 2]
            d = ord(d) - 87 if d >= 'a' else int(d)
            xa = c_uint(a)
            d = xa >> d if b[c + 1] == '+' else xa << d
            a = a + d & 4294967295 if b[c] == '+' else a ^ d
        return c_int(a)

    a = b

    for di in d:
        a = RL(a + di, "+-a^+6")

    a = RL(a, "+-3^+b+-f")
    a ^= tkk[1]
    a = a if a >= 0 else ((a & 2147483647) + 2147483648)
    a %= pow(10, 6)

    tk = '{0:d}.{1:d}'.format(a, a ^ b)
    return tk
"""

In [0]:
# a file named "geek", will be opened with the reading mode.
file = open(Package_path+'/textblob/translate.py', 'w')
# This will print every line one by one in the file pythonEnv-9e747e87-0295-4245-a50b-265e3d9446ae
file.write(t)
file.close()

In [0]:
from googletrans import Translator
import re
from langdetect import detect
import emoji
from pyspark.sql.functions import col, udf
from pyspark.sql.types import StringType,BooleanType,DateType,FloatType,DateType,LongType
import html
from nltk import word_tokenize
import string
from pyspark.sql.functions import *
from textblob import TextBlob
from textblob.sentiments import NaiveBayesAnalyzer

In [0]:
spark.conf.set("shuffle.service.enabled", "true")

In [0]:
spark.conf.set("spark.sql.shuffle.partitions",10000)

In [0]:
spark.conf.set("spark.sql.files.maxPartitionBytes", 10000)

In [0]:
df = spark.sql('select * from cloning.twitter_api')
df.display()

_c0 Datetime TweetId content lang mentionedUser hashtags retweet like replyCount Username followersCount verified leader 0 2023-01-05T04:26:03.000+0000 1610855118152536064 ஈரோடு சட்டமன்ற உறுப்பினர் 
திருமகன் ஈவேரா அவர்களின் திடீர் மறைவு செய்தி மிகுந்த வேதனை அளிக்கிறது. அன்னாரது ஆன்மா சாந்தியடைய எல்லாம் வல்ல இறைவனை வேண்டுகிறேன் அவரை இழந்து வாடும் குடும்பத்தினருக்கு ஆழ்ந்த இரங்கலை தெரிவித்துக் கொள்கிறேன் ta null null 5 59 0 NainarBJP 59354 false Nainar Nagenthiran 1 2023-01-04T07:59:27.000+0000 1610546436302831616 Today morning when Indian medical students enthusiastically welcomed in Manila, the capital of the Philippines which was organised by Dr. Gunasekar Ariyamuthu at the Philippines Airport under the leadership of BJP State Vice President Mr. Chakravarthy.
@BJP4India @BJP4TamilNadu https://t.co/PLl9e3mM7A en ['BJP4India', 'BJP4TamilNadu'] null 16 95 3 NainarBJP 59354 false Nainar Nagenthiran 2 2023-01-03T06:55:44.000+0000 1610168014229614593 தாய்மண்ணை காக்க ஆளவந்த ஆங்கிலேயரை எதிர்த்து போர்க்கொடி உயர்த்தி சுதந்திர விதையை விதைத்தவரும், வானம் பொழியுது பூமி விளையுது மன்னன் காணிக்கு வரி ஏன் செலுத்தவேண்டும் என வினாவிய வீரபாண்டிய கட்டபொம்மனின் பிறந்தநாளில் அவரது வீரத்தை போற்றி வணங்குகிறேன் https://t.co/XxJGyW4LVy ta null null 15 89 3 NainarBJP 59354 false Nainar Nagenthiran 3 2023-01-03T06:53:58.000+0000 1610167570338054144 வேலு நாச்சியார் வீரத்தை போற்றுவோம்....
இந்திய விடுதலை வரலாற்றில் வீரம் நிறைந்த வீரமங்கை வேலுநாச்சியாருக்கு ஈடாக எவரும் இல்லை,பெண் அடிமைத்தனம்,மூட நம்பிக்கை இதையெல்லாம் உடைத்தெறிந்து சிவகங்கை மண்ணை மீட்ட வீரமங்கை வேலுநாச்சியார் பிறந்த நாளில் அவரது வீரத்தை போற்றி வணங்குகிறேன். https://t.co/OlYXO8AFFC ta null null 20 130 4 NainarBJP 59354 false Nainar Nagenthiran 4 2023-01-01T03:14:58.000+0000 1609387680185614337 https://t.co/OEtfHW5kcu zxx null null 23 252 12 NainarBJP 59354 false Nainar Nagenthiran 5 2022-12-30T02:53:23.000+0000 1608657473870888961 @narendramodi Om Shanthi 🙏 hi ['narendramodi'] null 2 16 0 NainarBJP 59354 false Nainar Nagenthiran 6 2022-12-30T02:52:00.000+0000 1608657123784937472 The country is deeply saddened by the demise of the noble mother who gave the best leader to India.
My deepest condolences to Hon'ble Prime Minister of India Narendra Modi. @narendramodi on the loss of his mother Mrs.Heeraben. en ['narendramodi'] null 15 78 3 NainarBJP 59354 false Nainar Nagenthiran 7 2022-11-09T06:42:28.000+0000 1590233342427164673 Shri. Nainar Nagenthiran @NainarBJP, MLA & BJP Floor Leader- Tamilnadu Assembly called on me at my office @GoI_MeitY today. https://t.co/ZBvgsrgBJs en ['NainarBJP', 'GoI_MeitY'] null 80 140 0 Rajeev_GoI 311850 true Nainar Nagenthiran 8 2022-10-21T13:36:46.000+0000 1583452235933310978 DMK MLA and Tamil Nadu Assembly Speaker M. Appavu lowered the dignity of the house by taking ‘cow urine’ jibes at BJP MLA Nainar Nagenthiran. 
#DMK #TamilNadu #BJP #Appavu #NainarNagenthiran 
 https://t.co/Ox5b4wk9Bk en null ['DMK', 'TamilNadu', 'BJP', 'Appavu', 'NainarNagenthiran'] 7 15 1 TheCommuneMag 7169 false Nainar Nagenthiran 9 2022-07-18T08:48:39.000+0000 1548952880719093760 @NainarBJP Nandri Nainar Nagenthiran avargale. ht ['NainarBJP'] null 2 19 1 CTRavi_BJP 334818 true Nainar Nagenthiran 10 2022-07-05T13:30:59.000+0000 1544312888718147584 தமிழ்நாட்டைப் பிரிக்க மக்கள் கேட்டார்களா?

https://t.co/WciCN2SQmv | @NainarBJP | #Tamilnadu | #NainarNagenthiran | @BJP4TamilNadu | @BJP4India | @arivalayam | @Elangovantks | #TKSElangovan | #News7Tamil | #News7TamilUpdates https://t.co/KdFx6NZMZg ta ['NainarBJP', 'BJP4TamilNadu', 'BJP4India', 'arivalayam', 'Elangovantks'] ['Tamilnadu', 'NainarNagenthiran', 'TKSElangovan', 'News7Tamil', 'News7TamilUpdates'] 6 41 6 news7tamil 2162383 true Nainar Nagenthiran 11 2022-07-05T10:45:32.000+0000 1544271252986429441 #JustIn | "தமிழ்நாட்டை இரண்டாக பிரிங்க.." - பாஜக எம்.எல்.ஏ நயினார் நாகேந்திரன் சர்ச்சை பேச்சு

#Sunnews | #NainarNagenthiran | #TamilNadu https://t.co/ovNQSRknrW ta null ['JustIn', 'Sunnews', 'NainarNagenthiran', 'TamilNadu'] 37 160 136 sunnewst

In [0]:
df = df.drop('_c0')
display(df)

Datetime TweetId content lang mentionedUser hashtags retweet like replyCount Username followersCount verified leader 2023-01-05T04:26:03.000+0000 1610855118152536064 ஈரோடு சட்டமன்ற உறுப்பினர் 
திருமகன் ஈவேரா அவர்களின் திடீர் மறைவு செய்தி மிகுந்த வேதனை அளிக்கிறது. அன்னாரது ஆன்மா சாந்தியடைய எல்லாம் வல்ல இறைவனை வேண்டுகிறேன் அவரை இழந்து வாடும் குடும்பத்தினருக்கு ஆழ்ந்த இரங்கலை தெரிவித்துக் கொள்கிறேன் ta null null 5 59 0 NainarBJP 59354 false Nainar Nagenthiran 2023-01-04T07:59:27.000+0000 1610546436302831616 Today morning when Indian medical students enthusiastically welcomed in Manila, the capital of the Philippines which was organised by Dr. Gunasekar Ariyamuthu at the Philippines Airport under the leadership of BJP State Vice President Mr. Chakravarthy.
@BJP4India @BJP4TamilNadu https://t.co/PLl9e3mM7A en ['BJP4India', 'BJP4TamilNadu'] null 16 95 3 NainarBJP 59354 false Nainar Nagenthiran 2023-01-03T06:55:44.000+0000 1610168014229614593 தாய்மண்ணை காக்க ஆளவந்த ஆங்கிலேயரை எதிர்த்து போர்க்கொடி உயர்த்தி சுதந்திர விதையை விதைத்தவரும், வானம் பொழியுது பூமி விளையுது மன்னன் காணிக்கு வரி ஏன் செலுத்தவேண்டும் என வினாவிய வீரபாண்டிய கட்டபொம்மனின் பிறந்தநாளில் அவரது வீரத்தை போற்றி வணங்குகிறேன் https://t.co/XxJGyW4LVy ta null null 15 89 3 NainarBJP 59354 false Nainar Nagenthiran 2023-01-03T06:53:58.000+0000 1610167570338054144 வேலு நாச்சியார் வீரத்தை போற்றுவோம்....
இந்திய விடுதலை வரலாற்றில் வீரம் நிறைந்த வீரமங்கை வேலுநாச்சியாருக்கு ஈடாக எவரும் இல்லை,பெண் அடிமைத்தனம்,மூட நம்பிக்கை இதையெல்லாம் உடைத்தெறிந்து சிவகங்கை மண்ணை மீட்ட வீரமங்கை வேலுநாச்சியார் பிறந்த நாளில் அவரது வீரத்தை போற்றி வணங்குகிறேன். https://t.co/OlYXO8AFFC ta null null 20 130 4 NainarBJP 59354 false Nainar Nagenthiran 2023-01-01T03:14:58.000+0000 1609387680185614337 https://t.co/OEtfHW5kcu zxx null null 23 252 12 NainarBJP 59354 false Nainar Nagenthiran 2022-12-30T02:53:23.000+0000 1608657473870888961 @narendramodi Om Shanthi 🙏 hi ['narendramodi'] null 2 16 0 NainarBJP 59354 false Nainar Nagenthiran 2022-12-30T02:52:00.000+0000 1608657123784937472 The country is deeply saddened by the demise of the noble mother who gave the best leader to India.
My deepest condolences to Hon'ble Prime Minister of India Narendra Modi. @narendramodi on the loss of his mother Mrs.Heeraben. en ['narendramodi'] null 15 78 3 NainarBJP 59354 false Nainar Nagenthiran 2022-11-09T06:42:28.000+0000 1590233342427164673 Shri. Nainar Nagenthiran @NainarBJP, MLA & BJP Floor Leader- Tamilnadu Assembly called on me at my office @GoI_MeitY today. https://t.co/ZBvgsrgBJs en ['NainarBJP', 'GoI_MeitY'] null 80 140 0 Rajeev_GoI 311850 true Nainar Nagenthiran 2022-10-21T13:36:46.000+0000 1583452235933310978 DMK MLA and Tamil Nadu Assembly Speaker M. Appavu lowered the dignity of the house by taking ‘cow urine’ jibes at BJP MLA Nainar Nagenthiran. 
#DMK #TamilNadu #BJP #Appavu #NainarNagenthiran 
 https://t.co/Ox5b4wk9Bk en null ['DMK', 'TamilNadu', 'BJP', 'Appavu', 'NainarNagenthiran'] 7 15 1 TheCommuneMag 7169 false Nainar Nagenthiran 2022-07-18T08:48:39.000+0000 1548952880719093760 @NainarBJP Nandri Nainar Nagenthiran avargale. ht ['NainarBJP'] null 2 19 1 CTRavi_BJP 334818 true Nainar Nagenthiran 2022-07-05T13:30:59.000+0000 1544312888718147584 தமிழ்நாட்டைப் பிரிக்க மக்கள் கேட்டார்களா?

https://t.co/WciCN2SQmv | @NainarBJP | #Tamilnadu | #NainarNagenthiran | @BJP4TamilNadu | @BJP4India | @arivalayam | @Elangovantks | #TKSElangovan | #News7Tamil | #News7TamilUpdates https://t.co/KdFx6NZMZg ta ['NainarBJP', 'BJP4TamilNadu', 'BJP4India', 'arivalayam', 'Elangovantks'] ['Tamilnadu', 'NainarNagenthiran', 'TKSElangovan', 'News7Tamil', 'News7TamilUpdates'] 6 41 6 news7tamil 2162383 true Nainar Nagenthiran 2022-07-05T10:45:32.000+0000 1544271252986429441 #JustIn | "தமிழ்நாட்டை இரண்டாக பிரிங்க.." - பாஜக எம்.எல்.ஏ நயினார் நாகேந்திரன் சர்ச்சை பேச்சு

#Sunnews | #NainarNagenthiran | #TamilNadu https://t.co/ovNQSRknrW ta null ['JustIn', 'Sunnews', 'NainarNagenthiran', 'TamilNadu'] 37 160 136 sunnewstamil 1865134 true Nainar Nagen

In [0]:
df.count()

Out[12]: 304088

In [0]:
df = df.na.drop(subset=['content']) 
df.display()

Datetime TweetId content lang mentionedUser hashtags retweet like replyCount Username followersCount verified leader 2023-01-05T04:26:03.000+0000 1610855118152536064 ஈரோடு சட்டமன்ற உறுப்பினர் 
திருமகன் ஈவேரா அவர்களின் திடீர் மறைவு செய்தி மிகுந்த வேதனை அளிக்கிறது. அன்னாரது ஆன்மா சாந்தியடைய எல்லாம் வல்ல இறைவனை வேண்டுகிறேன் அவரை இழந்து வாடும் குடும்பத்தினருக்கு ஆழ்ந்த இரங்கலை தெரிவித்துக் கொள்கிறேன் ta null null 5 59 0 NainarBJP 59354 false Nainar Nagenthiran 2023-01-04T07:59:27.000+0000 1610546436302831616 Today morning when Indian medical students enthusiastically welcomed in Manila, the capital of the Philippines which was organised by Dr. Gunasekar Ariyamuthu at the Philippines Airport under the leadership of BJP State Vice President Mr. Chakravarthy.
@BJP4India @BJP4TamilNadu https://t.co/PLl9e3mM7A en ['BJP4India', 'BJP4TamilNadu'] null 16 95 3 NainarBJP 59354 false Nainar Nagenthiran 2023-01-03T06:55:44.000+0000 1610168014229614593 தாய்மண்ணை காக்க ஆளவந்த ஆங்கிலேயரை எதிர்த்து போர்க்கொடி உயர்த்தி சுதந்திர விதையை விதைத்தவரும், வானம் பொழியுது பூமி விளையுது மன்னன் காணிக்கு வரி ஏன் செலுத்தவேண்டும் என வினாவிய வீரபாண்டிய கட்டபொம்மனின் பிறந்தநாளில் அவரது வீரத்தை போற்றி வணங்குகிறேன் https://t.co/XxJGyW4LVy ta null null 15 89 3 NainarBJP 59354 false Nainar Nagenthiran 2023-01-03T06:53:58.000+0000 1610167570338054144 வேலு நாச்சியார் வீரத்தை போற்றுவோம்....
இந்திய விடுதலை வரலாற்றில் வீரம் நிறைந்த வீரமங்கை வேலுநாச்சியாருக்கு ஈடாக எவரும் இல்லை,பெண் அடிமைத்தனம்,மூட நம்பிக்கை இதையெல்லாம் உடைத்தெறிந்து சிவகங்கை மண்ணை மீட்ட வீரமங்கை வேலுநாச்சியார் பிறந்த நாளில் அவரது வீரத்தை போற்றி வணங்குகிறேன். https://t.co/OlYXO8AFFC ta null null 20 130 4 NainarBJP 59354 false Nainar Nagenthiran 2023-01-01T03:14:58.000+0000 1609387680185614337 https://t.co/OEtfHW5kcu zxx null null 23 252 12 NainarBJP 59354 false Nainar Nagenthiran 2022-12-30T02:53:23.000+0000 1608657473870888961 @narendramodi Om Shanthi 🙏 hi ['narendramodi'] null 2 16 0 NainarBJP 59354 false Nainar Nagenthiran 2022-12-30T02:52:00.000+0000 1608657123784937472 The country is deeply saddened by the demise of the noble mother who gave the best leader to India.
My deepest condolences to Hon'ble Prime Minister of India Narendra Modi. @narendramodi on the loss of his mother Mrs.Heeraben. en ['narendramodi'] null 15 78 3 NainarBJP 59354 false Nainar Nagenthiran 2022-11-09T06:42:28.000+0000 1590233342427164673 Shri. Nainar Nagenthiran @NainarBJP, MLA & BJP Floor Leader- Tamilnadu Assembly called on me at my office @GoI_MeitY today. https://t.co/ZBvgsrgBJs en ['NainarBJP', 'GoI_MeitY'] null 80 140 0 Rajeev_GoI 311850 true Nainar Nagenthiran 2022-10-21T13:36:46.000+0000 1583452235933310978 DMK MLA and Tamil Nadu Assembly Speaker M. Appavu lowered the dignity of the house by taking ‘cow urine’ jibes at BJP MLA Nainar Nagenthiran. 
#DMK #TamilNadu #BJP #Appavu #NainarNagenthiran 
 https://t.co/Ox5b4wk9Bk en null ['DMK', 'TamilNadu', 'BJP', 'Appavu', 'NainarNagenthiran'] 7 15 1 TheCommuneMag 7169 false Nainar Nagenthiran 2022-07-18T08:48:39.000+0000 1548952880719093760 @NainarBJP Nandri Nainar Nagenthiran avargale. ht ['NainarBJP'] null 2 19 1 CTRavi_BJP 334818 true Nainar Nagenthiran 2022-07-05T13:30:59.000+0000 1544312888718147584 தமிழ்நாட்டைப் பிரிக்க மக்கள் கேட்டார்களா?

https://t.co/WciCN2SQmv | @NainarBJP | #Tamilnadu | #NainarNagenthiran | @BJP4TamilNadu | @BJP4India | @arivalayam | @Elangovantks | #TKSElangovan | #News7Tamil | #News7TamilUpdates https://t.co/KdFx6NZMZg ta ['NainarBJP', 'BJP4TamilNadu', 'BJP4India', 'arivalayam', 'Elangovantks'] ['Tamilnadu', 'NainarNagenthiran', 'TKSElangovan', 'News7Tamil', 'News7TamilUpdates'] 6 41 6 news7tamil 2162383 true Nainar Nagenthiran 2022-07-05T10:45:32.000+0000 1544271252986429441 #JustIn | "தமிழ்நாட்டை இரண்டாக பிரிங்க.." - பாஜக எம்.எல்.ஏ நயினார் நாகேந்திரன் சர்ச்சை பேச்சு

#Sunnews | #NainarNagenthiran | #TamilNadu https://t.co/ovNQSRknrW ta null ['JustIn', 'Sunnews', 'NainarNagenthiran', 'TamilNadu'] 37 160 136 sunnewstamil 1865134 true Nainar Nagen

In [0]:
df.count()

Out[14]: 304060

In [0]:
df=df.drop_duplicates()
df.count()

Out[15]: 299225

In [0]:
df.rdd.getNumPartitions()

In [0]:
df.rdd.getNumPartitions()

In [0]:
df=df.repartition(10000)
df.show()

+-------------------+-------------------+--------------------+----+--------------------+--------------------+-------+----+----------+---------------+--------------+--------+-----------------+
|           Datetime|            TweetId|             content|lang|       mentionedUser|            hashtags|retweet|like|replyCount|       Username|followersCount|verified|           leader|
+-------------------+-------------------+--------------------+----+--------------------+--------------------+-------+----+----------+---------------+--------------+--------+-----------------+
|2016-10-05 07:52:41| 783575622467543040|Retweeted Chitra ...|null|        ['chitraSD']|       ['TamilNadu']|      0|   0|         0|      prasha_bp|           204|   false|            party|
|2021-09-18 15:20:50|1439248054188589057|_K and._K I am no...|null|['savukku', 'anna...|                null|      0|   0|         0|      drselvaid|             4|   false|            party|
|2022-01-11 19:00:08|1480977848533979138

In [0]:
df.rdd.getNumPartitions()

Out[23]: 10000

<h4>Data Cleaning</h4>

In [0]:
def Clean(t):
    try:
      m=t.split()
      l=detect(' '.join(m[0:2]))
      if l in ['ta','hi','te','kn','ml']:
        translator = TextBlob(t)
        t=str(translator.translate(to='en'))
      t = re.sub("@[A-Za-z0-9_]+","",t) #Remove @ sign
      t = re.sub('#+','',t)
      t = re.sub(r"(?:\@|http?\://|https?\://|www)\S+", "", t) #Remove http links
      t = re.sub(r'(:[!_\-\w]+:)', '', t)
      t = re.sub(r'[\?\.\!]+(?=[\?\.\!])',"",t)
      t=re.sub(r"(.)\1+",r"\1\1",t)
    except:
      Lan_det='null'
#     if l in ['qme','und','tl','in','ht','et'] and t!='':
#       try:
#         translator = TextBlob(t)
#         t=str(translator.translate(to='en'))
#       except:
#         pass
    
    t = " ".join(t.split())
    t =  emoji.demojize(t)
    t=re.sub("[:_]", " ", t)
    return t

In [0]:
Clean('தங்களது தொகுதியில் மிக நன்றாக களப்பணி செய்து வரும் பா.ஜ.க எம்.எல்.ஏக்கள் ! 👍')

Out[40]: 'BJP MLAs who are doing very good field work in their constituency!  thumbs up '

In [0]:
DataCleanUDF = udf(lambda x:Clean(x),StringType())   

In [0]:
df2= df.withColumn("content", DataCleanUDF(col("content")))
df2.display()

Datetime TweetId content lang mentionedUser hashtags retweet like replyCount Username followersCount verified leader 2017-10-22T11:12:45.000+0000 922058138538295297 3yearsofBlockbusterKaththi.yes, Tamilian should lead Tamil Nadu., do not bow down to the bullying of BJP.Tamils support Truth! null ['Vijay'] ['3yearsofBlockbusterKaththi'] 1 3 0 TamilRatsaschi 24695 false party 2022-11-27T04:03:39.000+0000 1596716357332406273 A harvest of peace is produced from a seed of contentment peace symbol dove person in lotus position smiling face with smiling eyes cherry blossom tulip evergreen tree Wordle 526 4/6* white large square white large square yellow square white large square white large square white large square green square white large square white large square white large square green square white large square white large square green square green square Wordle526 en ['Nur_e_Hina', 'Shahid_H_Raja', 'Shan_zyyy', 'DegrassiHigh2', 'khantanveer', 'Plato00009', 'sadafmedic', 'SheddingExtra'] ['Wordle526'] 0 4 0 Yasir_Nasim 121 false H Raja 2021-04-04T04:16:27.000+0000 1378562082262507525 She is campaigning for Kamalhasan, B-team of BJP in Tamilnadu. Irony. Please don't post as if she is very great and sorry, LDF will do much better without these pseudo seculars acknowledgement. null ['Irfanulhakeem'] null 0 4 0 Navneethan4 15 false party 2022-03-16T05:14:28.000+0000 1503962882081697794 Loosu thanama olaradha If you can answer for this If ur caste voted in Tamilnadu for bjp and you didn't get any central minister and BJP said ur equivalent caste got minister will you accept it. null ['RathinamVimal'] null 1 2 1 Thirusabare10 732 false party 2021-07-21T16:45:54.000+0000 1417888575371108353 MKStalin managed it so well that we were able to Oxygen situation in TamilNadu in a very proactive manner , Spokesperson, DMK, tells Navika Kumar on . , National Spokesperson, BJP responds. | IndiaWantsO2Truth null ['thenewshour', 'gauravbh'] ['MKStalin', 'Oxygen', 'TamilNadu', 'IndiaWantsO2Truth'] 2 21 3 TimesNow 10308366 true party 2022-07-16T07:19:12.000+0000 1548205593483022338 A teaser video for the upcoming 44th edition of the Chess Olympiad, hosted in Tamil Nadu this year, has stoked a row with state BJP chief calling the ad "all show and substance" as it does not feature sporting the country's ace player Vishwanathan Anand.… null null null 0 0 0 RSAliOfficial 725 false party 2021-03-08T11:44:39.000+0000 1368890403299061762 BREAKING Stalin, Stalin's son Udhayanidhi's constituency BJP is fielding! The list has just been released! BJP DMK MKStalin UdhayanidhiStalin CHENNAI TAMILNADU DMK Stalin TNEllection2021 Politics TNAssemblyElection2021 null null ['BREAKING', 'BJP', 'DMK', 'MKStalin', 'UdhayanidhiStalin', 'CHENNAI', 'TAMILNADU', 'திமுக', 'ஸ்டாலின்', 'TNElection2021', 'Politics', 'TNAssemblyElection2021'] 0 0 0 seithipunal 5778 false party 2018-12-20T11:42:38.000+0000 1075718112563982336 Modi sir. BJP should come to power in Tamil Nadu null ['narendramodi', 'BJP4Haryana', 'mlkhattar'] null 0 0 0 ThalaVR47 6 false party 2021-08-17T08:11:09.000+0000 1427543508819324946 Sekar Babu replies to Subramanian Swamy If Karunanidhi made a mistake, Stalin will also make the same mistake. Minister replies to Swamy! – minister sekar babu replies bjp subramanian swamy on priest appointment issue in temples tamil nadu null null null 0 1 0 rakeshrc99 204 false party 2021-09-09T15:01:17.000+0000 1435981643085324291 “Continue to work hard to use your education for the benefit of others, society and country.- Mr. Venkaiah Naidu VISIT NarendraModi Modi BJP BJP NarendraModi Modi VenkaiahNaidu Tamilnadu Tamilnews TamilnaduNews null null ['வெங்கையா_நாயுடு', 'நரேந்திரமோடி', 'மோடி', 'பாஜக', 'BJP', 'NarendraModi', 'Modi', 'VenkaiahNaidu', 'Tamilnadu', 'Tamilnews', 'TamilnaduNews'] 0 1 0 AmNews_Tamil 753 false party 2023-01-05T23:30:22.000+0000 1611143097345527808 Andi Moodevi this photo was taken by bjp or did he go alone to Annamalai. fortunately an ethereal party li

In [0]:
df2.count()

Out[59]: 299225

In [0]:
df3 = df2.na.drop(subset=['content']) 
df3.display()

Datetime TweetId content lang mentionedUser hashtags retweet like replyCount Username followersCount verified leader 2017-10-22T11:12:45.000+0000 922058138538295297 3yearsofBlockbusterKaththi.yes, Tamilian should lead Tamil Nadu., do not bow down to the bullying of BJP.Tamils support Truth! null ['Vijay'] ['3yearsofBlockbusterKaththi'] 1 3 0 TamilRatsaschi 24695 false party 2022-11-27T04:03:39.000+0000 1596716357332406273 A harvest of peace is produced from a seed of contentment peace symbol dove person in lotus position smiling face with smiling eyes cherry blossom tulip evergreen tree Wordle 526 4/6* white large square white large square yellow square white large square white large square white large square green square white large square white large square white large square green square white large square white large square green square green square Wordle526 en ['Nur_e_Hina', 'Shahid_H_Raja', 'Shan_zyyy', 'DegrassiHigh2', 'khantanveer', 'Plato00009', 'sadafmedic', 'SheddingExtra'] ['Wordle526'] 0 4 0 Yasir_Nasim 121 false H Raja 2021-04-04T04:16:27.000+0000 1378562082262507525 She is campaigning for Kamalhasan, B-team of BJP in Tamilnadu. Irony. Please don't post as if she is very great and sorry, LDF will do much better without these pseudo seculars acknowledgement. null ['Irfanulhakeem'] null 0 4 0 Navneethan4 15 false party 2022-03-16T05:14:28.000+0000 1503962882081697794 Loosu thanama olaradha If you can answer for this If ur caste voted in Tamilnadu for bjp and you didn't get any central minister and BJP said ur equivalent caste got minister will you accept it. null ['RathinamVimal'] null 1 2 1 Thirusabare10 732 false party 2021-07-21T16:45:54.000+0000 1417888575371108353 MKStalin managed it so well that we were able to Oxygen situation in TamilNadu in a very proactive manner , Spokesperson, DMK, tells Navika Kumar on . , National Spokesperson, BJP responds. | IndiaWantsO2Truth null ['thenewshour', 'gauravbh'] ['MKStalin', 'Oxygen', 'TamilNadu', 'IndiaWantsO2Truth'] 2 21 3 TimesNow 10308366 true party 2022-07-16T07:19:12.000+0000 1548205593483022338 A teaser video for the upcoming 44th edition of the Chess Olympiad, hosted in Tamil Nadu this year, has stoked a row with state BJP chief calling the ad "all show and substance" as it does not feature sporting the country's ace player Vishwanathan Anand.… null null null 0 0 0 RSAliOfficial 725 false party 2021-04-07T07:17:05.000+0000 1379694703185178632 189 *hutiye.same evm's are there in Kerala & Tamil Nadu.so BJP will win there also! null ['PiyushGoyal', 'narendramodi', 'AmitShah'] null 0 0 0 rickyguys06 22 false party 2019-03-04T11:53:13.000+0000 1102537477225697280 From Seven Sisters of N-E to Bihar - Maharashtra - Tamil Nadu - Punjab and Now Odissa. is weaving Fantastic Shawl that will secured "Never Before" Numbers to BJP Led NDA. JayPanda null ['RaghuramanMenon', 'AmitShah'] ['JayPanda'] 6 6 0 envee38 4078 false party 2022-12-22T02:02:21.000+0000 1605745527273885696 qme ['SuryahSG'] null 0 0 0 vmaniva03122857 86 false SuryahSG 2021-03-08T11:44:39.000+0000 1368890403299061762 BREAKING Stalin, Stalin's son Udhayanidhi's constituency BJP is fielding! The list has just been released! BJP DMK MKStalin UdhayanidhiStalin CHENNAI TAMILNADU DMK Stalin TNEllection2021 Politics TNAssemblyElection2021 null null ['BREAKING', 'BJP', 'DMK', 'MKStalin', 'UdhayanidhiStalin', 'CHENNAI', 'TAMILNADU', 'திமுக', 'ஸ்டாலின்', 'TNElection2021', 'Politics', 'TNAssemblyElection2021'] 0 0 0 seithipunal 5778 false party 2018-12-20T11:42:38.000+0000 1075718112563982336 Modi sir. BJP should come to power in Tamil Nadu null ['narendramodi', 'BJP4Haryana', 'mlkhattar'] null 0 0 0 ThalaVR47 6 false party 2015-08-11T04:07:51.000+0000 630953749557579776 BeefBan in Maharashtra anti-Muslim, AlcoholBan in TamilNadu anti-Christian, dear BJP pick your soft target. null null ['BeefBan', 'AlcoholBan', 'TamilNadu', 'BJP'] 0 0 0 NudgeIndia 843 false party 2021-03-30T08:16:21.000+0000 1376810515331096578 BJP I

<h3>Sentiment Analysis<\h3>

In [0]:
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer

In [0]:
analyzer = SentimentIntensityAnalyzer()
def Sentiment(Txt):
  vs = analyzer.polarity_scores(Txt)
  score=vs['compound']
  if score >= 0.05:
    Tweet='Positive'
  elif  score >-0.05 and score < 0.05:
    Tweet='Nuetral'
  elif score <=-0.05:
    Tweet='Nagative'
  return Tweet

In [0]:
Sentiment("BJP MLAs are not too good in their constituency!  thumbs up ")

Out[14]: 'Nagative'

In [0]:
Sentiment('Good')

Out[13]: 'Positive'

In [0]:
Sentiment("Not good")

Out[31]: 'Nagative'

In [0]:
SenUDF = udf(lambda z:Sentiment(z),StringType())   

In [0]:
df3= df2.withColumn("Segmentation", SenUDF(col("content")))
df3.display()

Datetime TweetId content lang mentionedUser hashtags retweet like replyCount Username followersCount verified leader Segmentation 2021-04-07T07:17:05.000+0000 1379694703185178632 189 *hutiye.same evm's are there in Kerala & Tamil Nadu.so BJP will win there also! null ['PiyushGoyal', 'narendramodi', 'AmitShah'] null 0 0 0 rickyguys06 22 false party Positive 2019-03-04T11:53:13.000+0000 1102537477225697280 From Seven Sisters of N-E to Bihar - Maharashtra - Tamil Nadu - Punjab and Now Odissa. is weaving Fantastic Shawl that will secured "Never Before" Numbers to BJP Led NDA. JayPanda null ['RaghuramanMenon', 'AmitShah'] ['JayPanda'] 6 6 0 envee38 4078 false party Positive 2022-12-22T02:02:21.000+0000 1605745527273885696 qme ['SuryahSG'] null 0 0 0 vmaniva03122857 86 false SuryahSG Nuetral 2015-08-11T04:07:51.000+0000 630953749557579776 BeefBan in Maharashtra anti-Muslim, AlcoholBan in TamilNadu anti-Christian, dear BJP pick your soft target. null null ['BeefBan', 'AlcoholBan', 'TamilNadu', 'BJP'] 0 0 0 NudgeIndia 843 false party Positive 2021-03-30T08:16:21.000+0000 1376810515331096578 BJP IS ONLY FIGHTING WITH “NOTA” IN “KERALA” AND “TAMIL NADU” GoBackModi null ['DChaurasia2312'] ['GoBackModi'] 2 1 0 ramanlaljain03 1937 false party Nagative 2019-11-29T12:57:49.000+0000 1200398457715822593 Whatever happens BJP. where Even if it happens. Myirlatan comes to the fore. No BJP No Tamil Nadu null ['suressaswath100'] null 0 2 0 Gurutalks_san 1300 false party Nagative 2022-09-03T17:02:11.000+0000 1566109313546199040 Mitron, Trust me.She Joined BJP today in Tamilnadu. क्या कहते हो, अब तो दक्षिण फतह कर लेंगे ना हम. ! एक और बात इनका नाम AlishaAbdullah हैं. TamilnaduBJP null null ['BJP', 'AlishaAbdullah', 'TamilnaduBJP'] 0 2 0 Rahulk123d 3385 false party Positive 2021-03-08T11:44:39.000+0000 1368890403299061762 BREAKING Stalin, Stalin's son Udhayanidhi's constituency BJP is fielding! The list has just been released! BJP DMK MKStalin UdhayanidhiStalin CHENNAI TAMILNADU DMK Stalin TNEllection2021 Politics TNAssemblyElection2021 null null ['BREAKING', 'BJP', 'DMK', 'MKStalin', 'UdhayanidhiStalin', 'CHENNAI', 'TAMILNADU', 'திமுக', 'ஸ்டாலின்', 'TNElection2021', 'Politics', 'TNAssemblyElection2021'] 0 0 0 seithipunal 5778 false party Nuetral 2018-12-20T11:42:38.000+0000 1075718112563982336 Modi sir. BJP should come to power in Tamil Nadu null ['narendramodi', 'BJP4Haryana', 'mlkhattar'] null 0 0 0 ThalaVR47 6 false party Nuetral 2021-05-04T05:47:47.000+0000 1389456702135705607 BJP won in Assam, no reports of Violence DMK won in Tamilnadu no reports of violence Left won in Kerala no violence TMC won in West Bengal, so much violence has been unleashed and this lady was complaining about Fascism Somebody show her the mirror BengalViolence null null ['BengalViolence'] 8 18 0 TinderBox19 1141 false party Positive 2023-01-05T23:30:22.000+0000 1611143097345527808 Andi Moodevi this photo was taken by bjp or did he go alone to Annamalai. fortunately an ethereal party like you left behind. bjp is not your property ta ['Gayathri_R_'] null 0 0 0 jkrtikn 70 false Gayathri_R Nuetral 2021-08-17T08:11:09.000+0000 1427543508819324946 Sekar Babu replies to Subramanian Swamy If Karunanidhi made a mistake, Stalin will also make the same mistake. Minister replies to Swamy! – minister sekar babu replies bjp subramanian swamy on priest appointment issue in temples tamil nadu null null null 0 1 0 rakeshrc99 204 false party Nagative 2021-09-09T15:01:17.000+0000 1435981643085324291 “Continue to work hard to use your education for the benefit of others, society and country.- Mr. Venkaiah Naidu VISIT NarendraModi Modi BJP BJP NarendraModi Modi VenkaiahNaidu Tamilnadu Tamilnews TamilnaduNews null null ['வெங்கையா_நாயுடு', 'நரேந்திரமோடி', 'மோடி', 'பாஜக', 'BJP', 'NarendraModi', 'Modi', 'VenkaiahNaidu', 'Tamilnadu', 'Tamilnews', 'TamilnaduNews'] 0 1 0 AmNews_Tamil 753 false party Positive 2017-10-22T11:12:45.000+0000 922058138538295297 3yearsofBlockbusterKaththi.yes, Tamilian sho

In [0]:
df3.write.mode("overwrite").saveAsTable("default.leader_tweet_clean")

In [0]:
df3 = df3.repartition(10000)
# df3.rdd.getNumPartitions()# df3 = df3.repartition(10000)
# df3.rdd.getNumPartitions()